<a id="top"></a>

The aim of this notebook is to clean and prepare the data in the leavetimes dataset.  
The data will be used to build a predictive model that will predict the travel time for a bus route.

***

# Import Packages

In [1]:
import pandas as pd
import datetime
import matplotlib.pyplot as plt
import calendar
import numpy as np
import time

import sqlite3
from sqlalchemy import create_engine

***

# Bold Print Function

In [2]:
def print_bold(string):
    """
    Function to print a given string in bold text.
    """
    print("\033[1m" + string + "\033[0m")

***

# Load Original Data File

In [3]:
# load in original data file using pandas
# this may take a couple of minutes and can result in a memory error if many notebooks are in use
t1 = datetime.datetime.now()
df_leavetimes = pd.read_csv('/home/faye/data/original/rt_leavetimes_DB_2018.txt', sep=';',error_bad_lines=False)
diff = datetime.datetime.now() - t1
print(f"Time to read: {diff}")

MemoryError: Unable to allocate 6.10 GiB for an array with shape (7, 116949113) and data type float64

In [ ]:
# load in original data file using a feather file
t1 = datetime.datetime.now()
df_leavetimes = pd.read_feather('/home/faye/data/original/leavetimes.feather')
diff = datetime.datetime.now() - t1
print(f"Time to read: {diff}")

***

<a id="contents"></a>
# Contents

- [1. Data Quality Report](#data_quality_report)
    - [1.1. Overview of the Dataset](#overview)
    - [1.2. Feature Data Types](#feature_data_types)
    - [1.3. Duplicates and Constants](#duplicates_and_constants)
    - [1.4. Descriptive Statistics for Continuous Features](#desc_stats_continuous)
    - [1.5. Descriptive Statistics for Categorical Features](#desc_stats_categorical)
    - [1.6. Plotting Continuous Features](#plotting_continuous)
    - [1.7. Plotting Categorical Features](#plotting_categorical)
    - [1.8. Logical Integrity Check](#logical_integrity_check)
    
    
- [2. Data Quality Plan](#data_quality_plan)
    - [2.1. The Plan](#the_plan)
    - [2.2. Applying the Solutions](#applying_solutions)  
  
  
- [3. Transforming and Extending Features](#transforming_and_extending)
    - [3.1. Add feature: MONTH](#add_month)
    - [3.2. Add feature: DAYOFWEEK](#add_dayofweek)
    - [3.3. Add feature: DWELLTIME](#add_dwelltime)
    - [3.4. Add feature: PLANNEDTIME_TRAVEL](#add_plannedtime_travel)
    - [3.5. Add feature: ACTUALTIME_TRAVEL](#add_actualtime_travel)
    - [3.6. Add feature: IS_HOLIDAY](#add_isholiday)
    - [3.7. Add feature: IS_WEEKDAY](#add_isweekday)
    

- [4. Saving to database](#db)

***

<a id="data_quality_report"></a>
# 1. Data Quality Report
[Back to contents](#contents)

<a id="overview"></a>
## 1.1. Overview of the Dataset
[Top of section](#data_quality_report)

> Each entry in the leavetimes dataset contains the actual data for one leave time of one vehicle at one stop point of a route.

In [4]:
# print the number of rows and features
num_rows = df_leavetimes.shape[0]
features = df_leavetimes.shape[1]
print(f"The dataset has {num_rows} rows with {features} features.")

The dataset has 116949113 rows with 18 features.


In [5]:
# print the first 5 rows of the dataset
print("The first 5 Rows are:")
df_leavetimes.head(5)

The first 5 Rows are:


DATASOURCE        DAYOFSERVICE   TRIPID  PROGRNUMBER  STOPPOINTID  \
0         DB  01-JAN-18 00:00:00  5972116           12          119   
1         DB  01-JAN-18 00:00:00  5966674           12          119   
2         DB  01-JAN-18 00:00:00  5959105           12          119   
3         DB  01-JAN-18 00:00:00  5966888           12          119   
4         DB  01-JAN-18 00:00:00  5965960           12          119   

   PLANNEDTIME_ARR  PLANNEDTIME_DEP  ACTUALTIME_ARR  ACTUALTIME_DEP  \
0            48030            48030           48012           48012   
1            54001            54001           54023           54023   
2            60001            60001           59955           59955   
3            58801            58801           58771           58771   
4            56401            56401           56309           56323   

   VEHICLEID  PASSENGERS  PASSENGERSIN  PASSENGERSOUT  DISTANCE  SUPPRESSED  \
0    2693211         NaN           NaN            NaN       NaN         NaN   
1    2693267         NaN           NaN            NaN       NaN         NaN   
2    2693263         NaN           NaN            NaN       NaN         NaN   
3    2693284         NaN           NaN            NaN       NaN         NaN   
4    2693209         NaN           NaN            NaN       NaN         NaN   

   JUSTIFICATIONID          LASTUPDATE  NOTE  
0              NaN  08-JAN-18 17:21:10   NaN  
1              NaN  08-JAN-18 17:21:10   NaN  
2              NaN  08-JAN-18 17:21:10   NaN  
3              NaN  08-JAN-18 17:21:10   NaN  
4              NaN  08-JAN-18 17:21:10   NaN

In [6]:
# print the last 5 rows of the dataset
print("The last 5 Rows are:")
df_leavetimes.tail(5)

The last 5 Rows are:


DATASOURCE        DAYOFSERVICE   TRIPID  PROGRNUMBER  STOPPOINTID  \
116949108         DB  31-DEC-18 00:00:00  8588153           78         4383   
116949109         DB  31-DEC-18 00:00:00  8587459           78         4383   
116949110         DB  31-DEC-18 00:00:00  8586183           78         4383   
116949111         DB  31-DEC-18 00:00:00  8589374           23         7053   
116949112         DB  31-DEC-18 00:00:00  8589372           24         2088   

           PLANNEDTIME_ARR  PLANNEDTIME_DEP  ACTUALTIME_ARR  ACTUALTIME_DEP  \
116949108            28605            28605           28998           29013   
116949109            22695            22695           23247           23247   
116949110            51481            51481           52237           52283   
116949111            53659            53659           53525           53525   
116949112            46383            46383           46315           46325   

           VEHICLEID  PASSENGERS  PASSENGERSIN  PASSENGERSOUT  DISTANCE  \
116949108    3265721         NaN           NaN            NaN       NaN   
116949109    3265687         NaN           NaN            NaN       NaN   
116949110    2693229         NaN           NaN            NaN       NaN   
116949111    3265669         NaN           NaN            NaN       NaN   
116949112    3265669         NaN           NaN            NaN       NaN   

           SUPPRESSED  JUSTIFICATIONID          LASTUPDATE  NOTE  
116949108         NaN              NaN  16-JAN-19 18:27:21   NaN  
116949109         NaN              NaN  16-JAN-19 18:27:21   NaN  
116949110         NaN              NaN  16-JAN-19 18:27:21   NaN  
116949111         NaN              NaN  16-JAN-19 18:27:21   NaN  
116949112         NaN              NaN  16-JAN-19 18:27:21   NaN

***

<a id="feature_data_types"></a>
## 1.2. Feature Data Types
[Top of section](#data_quality_report)

In [7]:
# print the data type for each feature
df_leavetimes.dtypes

DATASOURCE          object
DAYOFSERVICE        object
TRIPID               int64
PROGRNUMBER          int64
STOPPOINTID          int64
PLANNEDTIME_ARR      int64
PLANNEDTIME_DEP      int64
ACTUALTIME_ARR       int64
ACTUALTIME_DEP       int64
VEHICLEID            int64
PASSENGERS         float64
PASSENGERSIN       float64
PASSENGERSOUT      float64
DISTANCE           float64
SUPPRESSED         float64
JUSTIFICATIONID    float64
LASTUPDATE          object
NOTE               float64
dtype: object

- I am not concerned with the feature DATASOURCE so I will leave it as an object.  
- DAYOFSERVICE and LASTUPDATE are dates so I will convert these to datetime objects.  
- TRIPID, STOPPOINTID, and VEHICLEID are all unique ID numbers. I will convert these to type category.  
- PROGRNUMBER is the sequential position of the stop point in the trip. I will convert this to category.  
- PLANNEDTIME_ARR, PLANNEDTIME_DEP, ACTUALTIME_ARR, and ACTUALTIME_DEP are in unit seconds, I will leave these as int64 for the moment.  
- PASSENGERS, PASSENGERSIN, and PASSENGERSOUT describe the number of passengers on board, boarding, and descending. I will leave these features as float64.  
- DISTANCE describes the distance measured from the beginning of the trip, I will leave this as float64.  
- SUPPRESSED is a flag feature. If the leave time is planned and achieved, the record will contain both the planned and actual data. If the leave time is planned and suppressed, the record will contain only the planned data and the SUPRESSED flag will be checked. When the trip is partially suppressed it says the previous link is suppressed (0=achieved,1=suppressed).  
- The JUSTIFICATIONID feature is simply described as 'fault code' and listed as a number. I will examine this feature.
- The NOTE feature is described as 'free note', I will also need to examine this feature.

### 1.2.1. Convert DAYOFSERVICE and LASTUPDATE to datetime objects

In [8]:
# convert DAYOFSERVICE and LASTUPDATE to datetime object
df_leavetimes['DAYOFSERVICE'] = df_leavetimes['DAYOFSERVICE'].astype('datetime64')
df_leavetimes['LASTUPDATE'] = df_leavetimes['LASTUPDATE'].astype('datetime64')

### 1.2.2. Convert TRIPID, STOPPOINTID, VEHICLEID, and PROGRNUMBER to category

In [9]:
# convert the selected columns to type category
cols = ['TRIPID', 'STOPPOINTID', 'VEHICLEID', 'PROGRNUMBER']

for col in cols:
    df_leavetimes[col] = df_leavetimes[col].astype('category')

### 1.2.3. Convert SUPPRESSED to boolean

In [10]:
# convert SUPPRESSED to boolean
df_leavetimes['SUPPRESSED'] = df_leavetimes['SUPPRESSED'].astype('boolean')

### 1.2.4. Examine JUSTIFICATIONID and NOTE

#### JUSTIFICATIONID

In [11]:
# print the unique values of the JUSTIFICATIONID feature
df_leavetimes['JUSTIFICATIONID'].unique()

array([           nan, 4.84981386e+17, 4.84981386e+17, ...,
       4.84981387e+17, 4.84981387e+17, 4.84981387e+17])

In [12]:
# print the number of unique values for the JUSTIFICATIONID feature
len(df_leavetimes['JUSTIFICATIONID'].unique())

34966

> In the Concept Design document for the database, from which this data has come, we see that JUSTIFICATIONID is used as a foreign key to link to a justifications table whose data we do not have.  
As we are missing the key data to which this feature relates I believe it will be unusable for modelling an there for I will drop this feature later. 
For the moment I will convert this feature to type category as it is a unique identification number.

In [13]:
# convert JUSTIFICATIONID to type category
df_leavetimes['JUSTIFICATIONID'] = df_leavetimes['JUSTIFICATIONID'].astype('category')

#### NOTE

In [14]:
# print the unique values for the NOTE feature
df_leavetimes['NOTE'].unique()

array([nan])

> The NOTE feature is a constant column of missing values. This will be dealt with later so I will leave the data type as float64.

### 1.2.5. Converted Feature Data Types

In [15]:
# display the datatype of each feature
df_leavetimes.dtypes

DATASOURCE                 object
DAYOFSERVICE       datetime64[ns]
TRIPID                   category
PROGRNUMBER              category
STOPPOINTID              category
PLANNEDTIME_ARR             int64
PLANNEDTIME_DEP             int64
ACTUALTIME_ARR              int64
ACTUALTIME_DEP              int64
VEHICLEID                category
PASSENGERS                float64
PASSENGERSIN              float64
PASSENGERSOUT             float64
DISTANCE                  float64
SUPPRESSED                boolean
JUSTIFICATIONID          category
LASTUPDATE         datetime64[ns]
NOTE                      float64
dtype: object

In [16]:
# select all categorical columns
categorical_columns = df_leavetimes[
    ['DATASOURCE', 'TRIPID', 'PROGRNUMBER', 'STOPPOINTID', 
     'VEHICLEID', 'SUPPRESSED', 'JUSTIFICATIONID'
    ]
].columns

In [17]:
# select all continuous columns
continuous_columns = df_leavetimes[
    ['DAYOFSERVICE', 'PLANNEDTIME_ARR', 'PLANNEDTIME_DEP', 'ACTUALTIME_ARR', 'ACTUALTIME_DEP', 
     'PASSENGERS', 'PASSENGERSIN', 'PASSENGERSOUT', 'DISTANCE', 'LASTUPDATE', 'NOTE']
].columns

***

<a id="duplicates_and_constants"></a>
## 1.3. Duplicates and Constants
[Top of section](#data_quality_report)

### 1.3.1. Duplicate Rows

In [ ]:
# Find number of duplicate rows
num_duplicate_rows = df_leavetimes.duplicated().sum()
print(f"There are {num_duplicate_rows} duplicated rows in this dataset (excluding the first row).")
num_duplicate_rows_inclusive = df_leavetimes[df_leavetimes.duplicated(keep=False)].shape[0]
print(f"There are {num_duplicate_rows_inclusive} duplicated rows in this dataset (including row that is duplicated).")

> There are no duplicate rows in this dataset.

### 1.3.2. Duplicate Columns

> There does not appear to be any duplicate columns in this dataset

### 1.3.3. Constant Columns

In [ ]:
# Print Categorical Descriptive Statistics
df_leavetimes[categorical_columns].describe().T

> From this we see that DATASOURCE is a constant column as it only has 1 unique value, this will be dropped.

In [ ]:
# Check that the continuous features have a standard deviation greater than zero
df_leavetimes[continuous_columns].std()

> From the standard deviation of the continuous features above we can see that PASSENGERS, PASSENGERSIN, PASSENGERSOUT, DISTANCE, and NOTE are constant columns of null values, these will be dropped.

### 1.3.4. Drop Constant Columns

In [ ]:
# drop constant columns
constant_columns = [
    'DATASOURCE', 'PASSENGERS', 'PASSENGERSIN', 'PASSENGERSOUT',
    'DISTANCE', 'NOTE'
]

df_leavetimes = df_leavetimes.drop(columns=constant_columns)

## Save Cleaned Data Frame - 1

In [ ]:
# reorder columns
reordered_columns = [
    'DAYOFSERVICE', 'LASTUPDATE', 'TRIPID', 'PROGRNUMBER', 'STOPPOINTID', 
    'VEHICLEID', 'JUSTIFICATIONID', 'SUPPRESSED',
    'PLANNEDTIME_ARR', 'ACTUALTIME_ARR', 
    'PLANNEDTIME_DEP', 'ACTUALTIME_DEP',    
]

df_leavetimes = df_leavetimes[reordered_columns]

In [ ]:
# save dataframe to csv
df_leavetimes.to_csv('/home/faye/data/leavetimes_cleaned_1.csv')

In [ ]:
# save dataframe to feather
df_leavetimes.to_feather('/home/faye/data/leavetimes_cleaned_1.feather')

# Load Cleaned Data (if needed)

In [3]:
# load in cleaned data from feather file
df_leavetimes = pd.read_feather('/home/faye/data/leavetimes_cleaned_1.feather')

In [4]:
df_leavetimes.shape

(116949113, 12)

In [4]:
df_leavetimes.head(5)

DAYOFSERVICE          LASTUPDATE   TRIPID PROGRNUMBER STOPPOINTID VEHICLEID  \
0   2018-01-01 2018-01-08 17:21:10  5972116          12         119   2693211   
1   2018-01-01 2018-01-08 17:21:10  5966674          12         119   2693267   
2   2018-01-01 2018-01-08 17:21:10  5959105          12         119   2693263   
3   2018-01-01 2018-01-08 17:21:10  5966888          12         119   2693284   
4   2018-01-01 2018-01-08 17:21:10  5965960          12         119   2693209   

  JUSTIFICATIONID  SUPPRESSED  PLANNEDTIME_ARR  ACTUALTIME_ARR  \
0             NaN        <NA>            48030           48012   
1             NaN        <NA>            54001           54023   
2             NaN        <NA>            60001           59955   
3             NaN        <NA>            58801           58771   
4             NaN        <NA>            56401           56309   

   PLANNEDTIME_DEP  ACTUALTIME_DEP  
0            48030           48012  
1            54001           54023  
2            60001           59955  
3            58801           58771  
4            56401           56323

In [5]:
df_leavetimes.dtypes

DAYOFSERVICE       datetime64[ns]
LASTUPDATE         datetime64[ns]
TRIPID                   category
PROGRNUMBER              category
STOPPOINTID              category
VEHICLEID                category
JUSTIFICATIONID          category
SUPPRESSED                boolean
PLANNEDTIME_ARR             int64
ACTUALTIME_ARR              int64
PLANNEDTIME_DEP             int64
ACTUALTIME_DEP              int64
dtype: object

<a id="desc_stats_continuous"></a>
## 1.4. Descriptive Statistics for Continuous Features
[Top of section](#data_quality_report)

In [ ]:
# Select columns containing continuous data
continuous_columns = df_leavetimes[
    ['DAYOFSERVICE', 'LASTUPDATE',
     'PLANNEDTIME_ARR', 'ACTUALTIME_ARR', 
     'PLANNEDTIME_DEP', 'ACTUALTIME_DEP']
].columns

### 1.4.1. Descriptive Statistics

In [ ]:
# print table with descriptive statistics for all the continuous features
continuous_feat_desc = df_leavetimes[continuous_columns].describe(datetime_is_numeric=True).T

print_bold("Descriptive Statistics for Continuous Features")
continuous_feat_desc

> From the min and max for DAYOFSERVICE we can see that the data ranges from the 1st January to 31st December for the year 2018. By looking at the percentiles it also appears that the data is evenly spread throughout the year.

In [ ]:
# convert the min ACTUALTIME_ARR and max ACTUALTIME_DEP to HH:MM:SS
print_bold("min ACTUALTIME_ARR and max ACTUALTIME_DEP")
print(datetime.timedelta(seconds=15974))
print(datetime.timedelta(seconds=97177))
# convert the median ACTUALTIME_ARR and ACTUALTIME_DEP to HH:MM:SS
print_bold("median for ACTUALTIME_ARR and ACTUALTIME_DEP")
print(datetime.timedelta(seconds=53511))
print(datetime.timedelta(seconds=53526))

> If we look at the min for ACTUALTIME_ARR and max for ACTUALTIME_DEP and convert the seconds to time we can see that the leave times range from 04:26 to 02:59 the following day. If we look at the median value for ACTUALTIME_ARR and ACTUALTIME_DEP it appears that the data is evenly spread throughout this range.

### 1.4.2. Range of Values

In [ ]:
# for each continuous feature display the range of values and the number of instances for the 15 most common values
for feat in continuous_columns:
    
    print_bold(feat)
    print("Range {} is: {}" .format( feat, (df_leavetimes[feat].max() - df_leavetimes[feat].min()) ) )
    print("-"*10)
    
    print_bold("{0:10.5} {1}" .format("Value", "Number of Instances") )
    print(df_leavetimes[feat].value_counts().nlargest(15), "\n\n\n")
    print("-"*50)

In [ ]:
# check for null values for each continuous feature
print_bold("The sum of null values for Continuous Features")
print("-"*50)
print(df_leavetimes[continuous_columns].isnull().sum())

> From the above we can that we have no null values for the continuous features.

In [ ]:
# print the cardinality of each continuous feature
features_cardinality = list(df_leavetimes[continuous_columns].columns.values)

print_bold("{0:35} {1}" .format("Feature","Cardinality") )
print("{0:35} {1}" .format("-------","-----------") )

for c in features_cardinality:
    print("{0:35} {1}" .format( c, (len(df_leavetimes[c].unique()))) )

> We can see from the cardinality for DAYOFSERVICE that we have almost a full years worth of data for the leavetimes.

<a id="desc_stats_categorical"></a>
## 1.5. Descriptive Statistics for Categorical Features
[Top of section](#data_quality_report)

In [ ]:
# Select columns containing continuous data
categorical_columns = df_leavetimes[
    ['TRIPID', 'PROGRNUMBER', 'STOPPOINTID', 'VEHICLEID', 
     'JUSTIFICATIONID', 'SUPPRESSED']
].columns

In [ ]:
# print the descriptive statistics for all the categorical features
categorical_feat_desc = df_leavetimes[categorical_columns].describe().T
categorical_feat_desc

In [ ]:
# check for null values for each categorical feature
print_bold("The sum of null values for Continuous Features")
print("-"*50)
print(df_leavetimes[categorical_columns].isnull().sum())

> From the above we can see that there is a very high number of entries with null values for the features JUSTIFICATIONID and SUPPRESSED.

In [ ]:
# print the % of null values for JUSTIFICATIONID and SUPPRESSED
print_bold("The percentage of null values for JUSTIFICATIONID and SUPPRESSED")
print("-"*50)
print("{:20}{:.2f}" .format("JUSTIFICATIONID", df_leavetimes['JUSTIFICATIONID'].isnull().sum() / df_leavetimes.shape[0] * 100) )
print("{:20}{:.2f}" .format("SUPPRESSED", df_leavetimes['SUPPRESSED'].isnull().sum() / df_leavetimes.shape[0] * 100) )

> We have a extremely high number of missing values for both the JUSTIFICATIONID and SUPPRESSED feature.  
I don't believe JUSTIFICATIONID will prove useful for modelling due to the high number of missing values and the fact it references to data which we do not have.  
If we cannot infer the missing values for SUPPRESSED then I do not believe this feature will prove useful for any predictive modelling.

In [ ]:
# frequency table for categorical features
for feat in categorical_columns:
    title = "Frequency Table for " + feat + ":"
    print_bold(title)
    print("-"*50)
    print(df_leavetimes[feat].value_counts(normalize=True) * 100)
    print()

> Nearly three quarters of the values that we have for SUPPRESSED are False meaning the trips were achieved. 25% of these trips were suppressed. 

<a id="plotting_continuous"></a>
## 1.6. Plotting Continuous Features
[Top of section](#data_quality_report)

In [ ]:
# Plot histograms for continuous features
df_leavetimes[continuous_columns].hist(layout=(2, 2), figsize=(30,30), bins=12)
#plt.savefig('continuous_histograms_1-1.pdf')
plt.xlabel("Time (seconds)")
plt.show()

> From the plots above we can see that we have an increase in the number of entries where the arrival and departure times are around 30,000 and 60,000-70,000 seconds.

In [ ]:
# convert seconds to HH:MM:SS
print_bold("{:10}{}" .format("Seconds", "HH:MM:SS"))
print("{:<10}{}" .format(30000, datetime.timedelta(seconds=30000)))
print("{:<10}{}" .format(60000, datetime.timedelta(seconds=60000)))
print("{:<10}{}" .format(70000, datetime.timedelta(seconds=70000)))

> These times are roughly correspond with rush hour times.

<a id="plotting_categorical"></a>
## 1.7. Plotting Categorical Features
[Top of section](#data_quality_report)

> The only continuous feature I see any purpose in plotting is SUPPRESSED. I do not believe there is anything to gain from plotting the ID numbers or sequential stop number (PROGRNUMBER)

In [ ]:
# plot the feature SUPPRESSED
f = df_leavetimes['SUPPRESSED'].value_counts().plot(kind='bar', figsize=(10,10))
plt.show()

<a id="logical_integrity_check"></a>
## 1.8. Logical Integrity Check
[Top of section](#data_quality_report)

### 1.8.1. Check 1: Check that LASTUPDATE > DAYOFSERVICE

In [ ]:
# create a dataframe for check 1
check_1 = df_leavetimes[['DAYOFSERVICE','LASTUPDATE']][df_leavetimes['LASTUPDATE']<df_leavetimes['DAYOFSERVICE']]
print(f"Number of rows failing the check: {check_1.shape[0]}")
check_1

### 1.8.2. Check 2: Check that ACTUALTIME_DEP > ACTUALTIME_ARR

In [6]:
# create a dataframe for check 2
check_2 = df_leavetimes[['ACTUALTIME_ARR','ACTUALTIME_DEP']][df_leavetimes['ACTUALTIME_DEP']<df_leavetimes['ACTUALTIME_ARR']]
print(f"Number of rows failing the check: {check_2.shape[0]}")
check_2

Number of rows failing the check: 3


ACTUALTIME_ARR  ACTUALTIME_DEP
74759275           46208           46207
81013777           39260           39258
86217868           71991           71989

In [ ]:
# print 
df_leavetimes.iloc[[74759275,81013777,86217868]]

<a id="data_quality_plan"></a>
# 2. Data Quality Plan
[Back to contents](#contents)

<a id="the_plan"></a>
## 2.1. The Plan
[Top of section](#data_quality_plan)

| Variable Name           | Data Quality Issue | Handling Strategy      |
| :---------------------- | :----------------- | :--------------------- |
| DAYOFSERVICE            | none               | do nothing             |
| LASTUPDATE              | irrelevant for modelling| drop feature      |
| TRIPID                  | none               | do nothing             |
| PROGRNUMBER             | none               | do nothing             |
| STOPPOINTID             | none               | do nothing             |
| VEHICLEID               | none               | do nothing             |
| JUSTIFICATIONID         | 99.5% missing values| drop feature          |
| SUPPRESSED              | 99.5% missing values| drop feature          |
| PLANNEDTIME_ARR         | none               | do nothing             |
| ACTUALTIME_ARR          | logical integrity  | swap with ACTUALTIME_DEP    |
| PLANNEDTIME_DEP         | none               | do nothing             |
| ACTUALTIME_DEP          | logical integrity  | swap with ACTUALTIME_ARR    |

<a id="applying_solutions"></a>
## 2.2. Applying the Solutions
[Top of section](#data_quality_plan)

### 2.2.1. Drop Features: LASTUPDATE, JUSTIFICATIONID, and SUPPRESSED

In [7]:
# drop features LASTUPDATE, JUSTIFICATIONID, and SUPPRESSED
df_leavetimes = df_leavetimes.drop(columns=['LASTUPDATE','JUSTIFICATIONID','SUPPRESSED'])

### 2.2.2. Swap illogical rows from Logical Integrity Check 2

In [8]:
# print rows failing logical integrity check
df_leavetimes[['ACTUALTIME_ARR','ACTUALTIME_DEP']].iloc[[74759275,81013777,86217868]]

ACTUALTIME_ARR  ACTUALTIME_DEP
74759275           46208           46207
81013777           39260           39258
86217868           71991           71989

In [9]:
# swap ACTUALTIME_ARR and ACTUALTIME_DEP values for illogical rows
for i in check_2.index:
    df_leavetimes['ACTUALTIME_ARR'][i] = check_2['ACTUALTIME_DEP'][i]
    df_leavetimes['ACTUALTIME_DEP'][i] = check_2['ACTUALTIME_ARR'][i]

/home/faye/.local/lib/python3.6/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
/home/faye/.local/lib/python3.6/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.


In [10]:
# check values have been swapped
df_leavetimes[['ACTUALTIME_ARR','ACTUALTIME_DEP']].iloc[[74759275,81013777,86217868]]

ACTUALTIME_ARR  ACTUALTIME_DEP
74759275           46207           46208
81013777           39258           39260
86217868           71989           71991

***

## Save Cleaned Data Frame - 2

In [11]:
# save dataframe to csv
df_leavetimes.to_csv('/home/faye/data/leavetimes_cleaned_2.csv')

In [ ]:
# save dataframe to feather
# !! doesn't work due to an index error
df_leavetimes.to_feather('/home/faye/data/leavetimes_cleaned_2.feather', index=False)

***

<a id="transforming_and_extending"></a>
# 3. Transforming and Extending Features
[Back to contents](#contents)

New features to add:
1. MONTH
2. DAYOFWEEK
3. DWELLTIME
4. PLANNEDTIME_TRAVEL
5. ACTUALTIME_TRAVEL
6. IS_HOLIDAY
7. IS_WEEKDAY

<a id="add_month"></a>
## 3.1. Add feature: MONTH
[Top of section](#transforming_and_extending)

In [14]:
# add feature MONTHOFSERVICE
df_leavetimes['MONTHOFSERVICE'] = df_leavetimes['DAYOFSERVICE'].dt.strftime('%B')

<a id="add_dayofweek"></a>
## 3.2. Add feature: DAYOFWEEK
[Top of section](#transforming_and_extending)

In [7]:
# add feature DAYOFWEEK
df_leavetimes['DAYOFWEEK'] = [calendar.day_name[val.weekday()] for val in df_leavetimes['DAYOFSERVICE']]

<a id="add_dwelltime"></a>
## 3.3. Add feature: DWELLTIME
[Top of section](#transforming_and_extending)

In [9]:
# add feature DWELLTIME
df_leavetimes['DWELLTIME'] = df_leavetimes['ACTUALTIME_DEP'] - df_leavetimes['ACTUALTIME_ARR']

<a id="add_plannedtime_travel"></a>
## 3.4. Add feature: PLANNEDTIME_TRAVEL
[Top of section](#transforming_and_extending)

In [5]:
# sort sequentially by TRIPID, DAYOFSERVICE, PROGRNUMBER
df_leavetimes = df_leavetimes.sort_values(['TRIPID','DAYOFSERVICE','PROGRNUMBER'])

In [6]:
# calculate planned travel time
df_leavetimes['PLANNEDTIME_TRAVEL'] = (df_leavetimes['PLANNEDTIME_ARR']-df_leavetimes['PLANNEDTIME_DEP'].shift()).fillna(0)

<a id="add_actualtime_travel"></a>
## 3.5. Add feature: ACTUALTIME_TRAVEL
[Top of section](#transforming_and_extending)

In [8]:
# calculate planned travel time
df_leavetimes['ACTUALTIME_TRAVEL'] = (df_leavetimes['ACTUALTIME_ARR']-df_leavetimes['ACTUALTIME_DEP'].shift()).fillna(0)

<a id="add_isholiday"></a>
## 3.6. Add feature: IS_HOLIDAY
[Top of section](#transforming_and_extending)

In [10]:
import holidays

In [11]:
# Getting the Irish holidays - including bank holidays
# https://towardsdatascience.com/5-minute-guide-to-detecting-holidays-in-python-c270f8479387
irish_holidays_2018 = []
for date in holidays.Ireland(years=2018).items():
    irish_holidays_2018.append(str(date[0]))

In [12]:
# add feature IS_HOLIDAY
df_leavetimes['IS_HOLIDAY'] = [1 if str(val).split()[0] in irish_holidays_2018 else 0 for val in df_leavetimes['DAYOFSERVICE']]

<a id="add_isweekday"></a>
## 3.7. Add feature: IS_WEEKDAY
[Top of section](#transforming_and_extending)

In [13]:
# add feature IS_WEEKDAY
df_leavetimes['IS_WEEKDAY'] = [1 if int(val.weekday()) < 5 else 0 for val in df_leavetimes['DAYOFSERVICE']]

***

# Reorder Columns and Save Dataset
[Back to contents](#contents)

In [26]:
# reorder columns
reorder_cols = [
    'DAYOFSERVICE', 'DAYOFWEEK', 'MONTHOFSERVICE', 'TRIPID', 'PROGRNUMBER', 'STOPPOINTID', 'VEHICLEID',
    'PLANNEDTIME_ARR', 'ACTUALTIME_ARR', 'PLANNEDTIME_DEP', 'ACTUALTIME_DEP', 'DWELLTIME',
    'PLANNEDTIME_TRAVEL', 'ACTUALTIME_TRAVEL', 'IS_HOLIDAY', 'IS_WEEKDAY'
]

df_leavetimes = df_leavetimes[reorder_cols]

In [30]:
# save dataframe to csv
df_leavetimes.to_csv('/home/faye/data/leavetimes_extra_features.csv')

In [ ]:
# save dataframe to feather
df_leavetimes.to_feather('/home/faye/data/leavetimes_extra_features.feather')

***

<a id="db"></a>
# 4. Save dataframe to DB
[Back to contents](#contents)

In [3]:
# create connection using 'create_engine' and then invoke 'connect'
db_engine = create_engine('sqlite:///dublinbus.db', echo=True)
#sqlite_connection = engine.connect()

In [41]:
# save df to sql table
sqlite_table = 'leavetimes'
#df_leavetimes.to_sql(sqlite_table, sqlite_connection, if_exists='fail')

In [27]:
def format_chunk(chunk, cont_cols, cat_cols):
    # drop column
    chunk = chunk.drop(columns=['Unnamed: 0'])
    
    # convert datetime
    chunk['DAYOFSERVICE'] = pd.to_datetime(chunk['DAYOFSERVICE'])

    # convert continuos columns 
    for col in cont_cols:
        chunk[col] = chunk[col].astype('int32')

    # convert categorical columns
    for col in cat_cols:
        chunk[col] = chunk[col].astype('category')

    return chunk

In [42]:
chunk_size=50000
batch_no=1

for chunk in pd.read_csv('/home/faye/data/leavetimes_extra_features.csv', chunksize=chunk_size, iterator=True):
    chunk = format_chunk(chunk, cont_cols, cat_cols)
    chunk.to_sql('leavetimes', db_engine, if_exists='append')
    batch_no+=1
    print('index: {}'.format(batch_no))

2021-07-09 11:35:59,380 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("leavetimes")
2021-07-09 11:35:59,381 INFO sqlalchemy.engine.Engine [raw sql] ()
2021-07-09 11:35:59,489 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2021-07-09 11:36:00,269 INFO sqlalchemy.engine.Engine INSERT INTO leavetimes ("index", "DAYOFSERVICE", "DAYOFWEEK", "MONTHOFSERVICE", "TRIPID", "PROGRNUMBER", "STOPPOINTID", "VEHICLEID", "PLANNEDTIME_ARR", "ACTUALTIME_ARR", "PLANNEDTIME_DEP", "ACTUALTIME_DEP", "DWELLTIME", "PLANNEDTIME_TRAVEL", "ACTUALTIME_TRAVEL", "IS_HOLIDAY", "IS_WEEKDAY") VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
2021-07-09 11:36:00,270 INFO sqlalchemy.engine.Engine [generated in 0.64835s] ((0, '2018-01-06 00:00:00.000000', 'Saturday', 'January', 5955221, 1, 248, 2693254, 37800, 37836, 37800, 37836, 0, 0, 0, 0, 0), (1, '2018-01-06 00:00:00.000000', 'Saturday', 'January', 5955221, 2, 249, 2693254, 37857, 37875, 37857, 37904, 29, 57, 39, 0, 0), (2, '2018-01-06 00:00:00.000000

2021-07-09 11:36:04,884 INFO sqlalchemy.engine.Engine COMMIT
index: 5
2021-07-09 11:36:05,005 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("leavetimes")
2021-07-09 11:36:05,007 INFO sqlalchemy.engine.Engine [raw sql] ()
2021-07-09 11:36:05,112 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2021-07-09 11:36:06,082 INFO sqlalchemy.engine.Engine INSERT INTO leavetimes ("index", "DAYOFSERVICE", "DAYOFWEEK", "MONTHOFSERVICE", "TRIPID", "PROGRNUMBER", "STOPPOINTID", "VEHICLEID", "PLANNEDTIME_ARR", "ACTUALTIME_ARR", "PLANNEDTIME_DEP", "ACTUALTIME_DEP", "DWELLTIME", "PLANNEDTIME_TRAVEL", "ACTUALTIME_TRAVEL", "IS_HOLIDAY", "IS_WEEKDAY") VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
2021-07-09 11:36:06,083 INFO sqlalchemy.engine.Engine [generated in 0.85514s] ((200000, '2018-01-05 00:00:00.000000', 'Friday', 'January', 5956958, 17, 675, 2693207, 37112, 37723, 37112, 37723, 0, 29, 10, 0, 1), (200001, '2018-01-05 00:00:00.000000', 'Friday', 'January', 5956958, 18, 4380, 269320

2021-07-09 11:36:10,677 INFO sqlalchemy.engine.Engine COMMIT
index: 9
2021-07-09 11:36:10,795 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("leavetimes")
2021-07-09 11:36:10,796 INFO sqlalchemy.engine.Engine [raw sql] ()
2021-07-09 11:36:10,898 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2021-07-09 11:36:11,657 INFO sqlalchemy.engine.Engine INSERT INTO leavetimes ("index", "DAYOFSERVICE", "DAYOFWEEK", "MONTHOFSERVICE", "TRIPID", "PROGRNUMBER", "STOPPOINTID", "VEHICLEID", "PLANNEDTIME_ARR", "ACTUALTIME_ARR", "PLANNEDTIME_DEP", "ACTUALTIME_DEP", "DWELLTIME", "PLANNEDTIME_TRAVEL", "ACTUALTIME_TRAVEL", "IS_HOLIDAY", "IS_WEEKDAY") VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
2021-07-09 11:36:11,658 INFO sqlalchemy.engine.Engine [generated in 0.64278s] ((400000, '2018-01-03 00:00:00.000000', 'Wednesday', 'January', 5958650, 8, 6229, 2406931, 62518, 62555, 62518, 62555, 0, 61, 61, 0, 1), (400001, '2018-01-03 00:00:00.000000', 'Wednesday', 'January', 5958650, 9, 6364, 2

2021-07-09 11:36:16,500 INFO sqlalchemy.engine.Engine COMMIT
index: 13
2021-07-09 11:36:16,618 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("leavetimes")
2021-07-09 11:36:16,619 INFO sqlalchemy.engine.Engine [raw sql] ()
2021-07-09 11:36:16,721 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2021-07-09 11:36:17,700 INFO sqlalchemy.engine.Engine INSERT INTO leavetimes ("index", "DAYOFSERVICE", "DAYOFWEEK", "MONTHOFSERVICE", "TRIPID", "PROGRNUMBER", "STOPPOINTID", "VEHICLEID", "PLANNEDTIME_ARR", "ACTUALTIME_ARR", "PLANNEDTIME_DEP", "ACTUALTIME_DEP", "DWELLTIME", "PLANNEDTIME_TRAVEL", "ACTUALTIME_TRAVEL", "IS_HOLIDAY", "IS_WEEKDAY") VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
2021-07-09 11:36:17,701 INFO sqlalchemy.engine.Engine [generated in 0.86212s] ((600000, '2018-01-01 00:00:00.000000', 'Monday', 'January', 5960454, 48, 523, 2693240, 51438, 50803, 51438, 50818, 15, 23, 14, 1, 1), (600001, '2018-01-01 00:00:00.000000', 'Monday', 'January', 5960454, 49, 669, 26932

2021-07-09 11:36:22,327 INFO sqlalchemy.engine.Engine COMMIT
index: 17
2021-07-09 11:36:22,443 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("leavetimes")
2021-07-09 11:36:22,444 INFO sqlalchemy.engine.Engine [raw sql] ()
2021-07-09 11:36:22,547 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2021-07-09 11:36:23,299 INFO sqlalchemy.engine.Engine INSERT INTO leavetimes ("index", "DAYOFSERVICE", "DAYOFWEEK", "MONTHOFSERVICE", "TRIPID", "PROGRNUMBER", "STOPPOINTID", "VEHICLEID", "PLANNEDTIME_ARR", "ACTUALTIME_ARR", "PLANNEDTIME_DEP", "ACTUALTIME_DEP", "DWELLTIME", "PLANNEDTIME_TRAVEL", "ACTUALTIME_TRAVEL", "IS_HOLIDAY", "IS_WEEKDAY") VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
2021-07-09 11:36:23,300 INFO sqlalchemy.engine.Engine [generated in 0.63546s] ((800000, '2018-01-02 00:00:00.000000', 'Tuesday', 'January', 5962266, 79, 4690, 2172297, 48642, 48141, 48642, 48141, 0, 91, 54, 0, 1), (800001, '2018-01-02 00:00:00.000000', 'Tuesday', 'January', 5962266, 80, 4411, 21

...

2021-07-09 13:07:40,959 INFO sqlalchemy.engine.Engine COMMIT
index: 2321
2021-07-09 13:07:41,779 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("leavetimes")
2021-07-09 13:07:41,780 INFO sqlalchemy.engine.Engine [raw sql] ()
2021-07-09 13:07:41,883 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2021-07-09 13:07:42,690 INFO sqlalchemy.engine.Engine INSERT INTO leavetimes ("index", "DAYOFSERVICE", "DAYOFWEEK", "MONTHOFSERVICE", "TRIPID", "PROGRNUMBER", "STOPPOINTID", "VEHICLEID", "PLANNEDTIME_ARR", "ACTUALTIME_ARR", "PLANNEDTIME_DEP", "ACTUALTIME_DEP", "DWELLTIME", "PLANNEDTIME_TRAVEL", "ACTUALTIME_TRAVEL", "IS_HOLIDAY", "IS_WEEKDAY") VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
2021-07-09 13:07:42,691 INFO sqlalchemy.engine.Engine [generated in 0.68612s] ((116000000, '2018-12-31 00:00:00.000000', 'Monday', 'December', 8584035, 54, 1077, 3088373, 76891, 76633, 76891, 76646, 13, 44, 52, 0, 1), (116000001, '2018-12-31 00:00:00.000000', 'Monday', 'December', 8584035, 55,

2021-07-09 13:07:51,896 INFO sqlalchemy.engine.Engine COMMIT
index: 2325
2021-07-09 13:07:52,456 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("leavetimes")
2021-07-09 13:07:52,457 INFO sqlalchemy.engine.Engine [raw sql] ()
2021-07-09 13:07:52,576 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2021-07-09 13:07:53,496 INFO sqlalchemy.engine.Engine INSERT INTO leavetimes ("index", "DAYOFSERVICE", "DAYOFWEEK", "MONTHOFSERVICE", "TRIPID", "PROGRNUMBER", "STOPPOINTID", "VEHICLEID", "PLANNEDTIME_ARR", "ACTUALTIME_ARR", "PLANNEDTIME_DEP", "ACTUALTIME_DEP", "DWELLTIME", "PLANNEDTIME_TRAVEL", "ACTUALTIME_TRAVEL", "IS_HOLIDAY", "IS_WEEKDAY") VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
2021-07-09 13:07:53,497 INFO sqlalchemy.engine.Engine [generated in 0.70707s] ((116200000, '2018-12-23 00:00:00.000000', 'Sunday', 'December', 8585753, 35, 1637, 2534846, 78218, 78594, 78218, 78623, 29, 39, 37, 0, 0), (116200001, '2018-12-23 00:00:00.000000', 'Sunday', 'December', 8585753, 36,

2021-07-09 13:08:06,246 INFO sqlalchemy.engine.Engine COMMIT
index: 2329
2021-07-09 13:08:06,768 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("leavetimes")
2021-07-09 13:08:06,770 INFO sqlalchemy.engine.Engine [raw sql] ()
2021-07-09 13:08:06,873 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2021-07-09 13:08:07,689 INFO sqlalchemy.engine.Engine INSERT INTO leavetimes ("index", "DAYOFSERVICE", "DAYOFWEEK", "MONTHOFSERVICE", "TRIPID", "PROGRNUMBER", "STOPPOINTID", "VEHICLEID", "PLANNEDTIME_ARR", "ACTUALTIME_ARR", "PLANNEDTIME_DEP", "ACTUALTIME_DEP", "DWELLTIME", "PLANNEDTIME_TRAVEL", "ACTUALTIME_TRAVEL", "IS_HOLIDAY", "IS_WEEKDAY") VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
2021-07-09 13:08:07,690 INFO sqlalchemy.engine.Engine [generated in 0.70001s] ((116400000, '2018-12-26 00:00:00.000000', 'Wednesday', 'December', 8587311, 26, 3077, 2868381, 53402, 53267, 53402, 53282, 15, 41, 19, 1, 1), (116400001, '2018-12-26 00:00:00.000000', 'Wednesday', 'December', 858731

2021-07-09 13:08:20,223 INFO sqlalchemy.engine.Engine COMMIT
index: 2333
2021-07-09 13:08:20,966 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("leavetimes")
2021-07-09 13:08:20,968 INFO sqlalchemy.engine.Engine [raw sql] ()
2021-07-09 13:08:21,123 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2021-07-09 13:08:22,396 INFO sqlalchemy.engine.Engine INSERT INTO leavetimes ("index", "DAYOFSERVICE", "DAYOFWEEK", "MONTHOFSERVICE", "TRIPID", "PROGRNUMBER", "STOPPOINTID", "VEHICLEID", "PLANNEDTIME_ARR", "ACTUALTIME_ARR", "PLANNEDTIME_DEP", "ACTUALTIME_DEP", "DWELLTIME", "PLANNEDTIME_TRAVEL", "ACTUALTIME_TRAVEL", "IS_HOLIDAY", "IS_WEEKDAY") VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
2021-07-09 13:08:22,398 INFO sqlalchemy.engine.Engine [generated in 1.10499s] ((116600000, '2018-12-24 00:00:00.000000', 'Monday', 'December', 8589298, 23, 1783, 2868407, 31308, 31576, 31308, 31583, 7, 28, 24, 0, 1), (116600001, '2018-12-24 00:00:00.000000', 'Monday', 'December', 8589298, 24, 

2021-07-09 13:08:31,921 INFO sqlalchemy.engine.Engine COMMIT
index: 2337
2021-07-09 13:08:32,355 INFO sqlalchemy.engine.Engine PRAGMA main.table_info("leavetimes")
2021-07-09 13:08:32,357 INFO sqlalchemy.engine.Engine [raw sql] ()
2021-07-09 13:08:32,461 INFO sqlalchemy.engine.Engine BEGIN (implicit)
2021-07-09 13:08:33,846 INFO sqlalchemy.engine.Engine INSERT INTO leavetimes ("index", "DAYOFSERVICE", "DAYOFWEEK", "MONTHOFSERVICE", "TRIPID", "PROGRNUMBER", "STOPPOINTID", "VEHICLEID", "PLANNEDTIME_ARR", "ACTUALTIME_ARR", "PLANNEDTIME_DEP", "ACTUALTIME_DEP", "DWELLTIME", "PLANNEDTIME_TRAVEL", "ACTUALTIME_TRAVEL", "IS_HOLIDAY", "IS_WEEKDAY") VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
2021-07-09 13:08:33,847 INFO sqlalchemy.engine.Engine [generated in 1.23020s] ((116800000, '2018-12-24 00:00:00.000000', 'Monday', 'December', 8590847, 28, 1966, 3265714, 37200, 37596, 37200, 37614, 18, 77, 58, 0, 1), (116800001, '2018-12-24 00:00:00.000000', 'Monday', 'December', 8590847, 29,

***

[Back to top](#top)